#Import Libraries

In [28]:
from bs4 import BeautifulSoup
import pandas as pd
import requests


In [2]:
import http.client as http_client
import logging
http_client.HTTPConnection.debuglevel = 0
logging.getLogger().setLevel(logging.WARNING)  # or logging.ERROR
requests_log = logging.getLogger("requests.packages.urllib3")
requests_log.setLevel(logging.WARNING)  # or logging.ERROR
requests_log.propagate = False

In [30]:
import postcodes_io_api
import logging
import requests
api1  = postcodes_io_api.Api(debug_http=False)

Extracting Report IDs

In [3]:
from bs4 import BeautifulSoup
import pandas as pd
import requests

i=1
b=1
df1 = pd.DataFrame()

url = 'https://fixmystreet.gloucestershire.gov.uk/reports/Gloucestershire?zoom=2&lat=51.84586&lon=-2.15136&p='+str(i)
#print(url)
#print(requests.get(url))
while requests.get(url).status_code== 200 and b==1:
    #print('a')
    #print(i)
    url = 'https://fixmystreet.gloucestershire.gov.uk/reports/Gloucestershire?zoom=2&lat=51.84586&lon=-2.15136&p='+str(i)
    #print(url)
    # Send a GET request to the URL
    response = requests.get(url)

    # Check if the request was successful (status code 200)
    if response.status_code == 200:
        # Parse the HTML content
        soup = BeautifulSoup(response.text, 'html.parser')
        #print(soup)
        # Extract all unique data-id attributes
        data_ids = set()
        #print(soup.find_all('img', {'class': 'pin js-pin'}))
        if soup.find_all('img', {'class': 'pin js-pin'}):
            b=1
        else:
            b=0
        
        for pin in soup.find_all('img', {'class': 'pin js-pin'}):
            data_id = pin.get('data-id')
           # print(pin)
            if data_id:
                data_ids.add(data_id)

        # Create a DataFrame
        df = pd.DataFrame({'data-id': list(data_ids)})


        # Concatenate the existing DataFrame and the new DataFrame
        df1 = pd.concat([df1, df], ignore_index=True)
        
        # Print the DataFrame
        print(i)
        i=i+1
        #print(df)


    else:
        print("Failed to retrieve the webpage. Status code:", response.status_code)


print(df1)


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
Failed to retrieve the webpage. Status code: 503
      data-id
0     5677669
1     5721855
2     5504443
3     5711940
4     5823867
...       ...
5795  5590459
5796  5631802
5797  5588653
5798  5593873
5799  5664031

[5800 rows x 1 columns]


Extracting Report Data

In [4]:
from bs4 import BeautifulSoup
import pandas as pd
import requests
import json
import datetime

# Get the current date and time
current_datetime = datetime.datetime.now()

# Print the date and time
#print(current_datetime)

i=str(df1.loc[0,'data-id'])
j=0
b=1
df3 = pd.DataFrame()
dict1=[]
#print(i)
url = "https://fixmystreet.gloucestershire.gov.uk/report/"+i
#print(url)
#print(requests.get(url))
#while requests.get(url).status_code== 200 and b==1:
while b==1:
    #b=b+1
    #df2 = pd.DataFrame()
    #print('a')
    #print(j)
    url = "https://fixmystreet.gloucestershire.gov.uk/report/"+i
    #print(url)
    # Send a GET request to the URL
    response = requests.get(url)

    # Check if the request was successful (status code 200)
    if response.status_code == 200:
        # Parse the HTML content
        soup = BeautifulSoup(response.text, 'html.parser')
        #print(soup)
        # Extract all unique data-id attributes
        data_ids = set()
        #print(soup.find_all('img', {'class': 'pin js-pin'}))
        
                
        latitude = soup.find('div', {'id': 'js-map-data'}).get('data-latitude')
        longitude= soup.find('div', {'id': 'js-map-data'}).get('data-longitude')
        problem_header = soup.find('div', {'class': 'problem-header clearfix'}).find('h1').text
        report_meta_info = soup.find('p',{'class':'report_meta_info'}).text
        moderate_display = soup.find('div',{'class':'moderate-display'}).find('p').text
        if soup.find('div',{'class':'banner'}) is None:
            banner='None'
        else:
            banner=soup.find('div',{'class':'banner'}).find('p').text
        updates_list = []
        k=1
        for pin in soup.find_all('li', {'class': 'item-list__item item-list__item--updates'}):
            updates_list1 = []
            updates_list2 = []
            #print(pin)
            #print(pin.find('a')['name'])
            update_number=pin.find('a')['name']
            for pin1 in pin.find_all('div', {'class': 'item-list__update-text'}):
            #print(pin1)
                m=1
                n=1
                for pin2 in pin1.find_all('div', {'class': 'moderate-display'}):
                    #print(pin2.text)
                    updates_list1.append({"update":n, "moderate_display": pin2.text})
                    n=n+1
                for pin3 in pin1.find_all('p',{'class':'meta-2'}):
                    #print(pin3.text)
                    updates_list2.append({"update":m, "meta_2": pin3.text})
                    m=m+1
            updates_list.append({"update_id":k,"update_number": update_number, "moderate_display": updates_list1, "meta_2": updates_list2})
            k=k+1
    
        report_dict = {
            "id": i,
            "current_datetime":str(current_datetime),
            "latitude":latitude,
            "longitude":longitude,
            "problem_header":problem_header,
            "report_meta_info":report_meta_info,
            "moderate_display":moderate_display,
            "banner":banner,
            "updates":updates_list
        }

        dict1.append(report_dict)
    
        #df2['latitude'] = [latitude]
        #df2['longitude'] = [longitude]
        #df2['problem_header'] = [problem_header]
        #df2['report_meta_info'] = [report_meta_info]
        #df2['moderate_display'] = [moderate_display]
        #df2['status']=[banner]


        # Concatenate the existing DataFrame and the new DataFrame
        #'df3 = pd.concat([df3, df2], ignore_index=True)
        
        # Print the DataFrame
        #print(i)
        j=j+1
        if j<=df1.index.argmax():
            if df1.loc[j,'data-id'] is None:
                b=0
                print('b1')
            else:
                i=str(df1.loc[j,'data-id'])
            #print(df2)
        else:
            b=0
            print('b2')


    else:
        print("Failed to retrieve the webpage. Status code:", response.status_code)
        print('/n ',url)
        j=j+1
        if j<=df1.index.argmax():
            if df1.loc[j,'data-id'] is None:
                b=0
                print('b3')
                #print(j)
            else:
                i=str(df1.loc[j,'data-id'])
            url = "https://fixmystreet.gloucestershire.gov.uk/report/"+i
        else:
            b=0
            print('b4')
print(j)        
report_data = {"reports": dict1}
json_string = json.dumps(report_data, indent=2)
#print(json_string)
#print(df3)


b2
5800


In [5]:
#report_data = {"reports": dict1}
#json_string = json.dumps(report_data, indent=2)
print(json_string)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [171]:
with open('output19.json', 'w') as json_file:
    json.dump(report_data, json_file, indent=2)

#Transform json to data frame

In [10]:
import json
import pandas as pd
from pandas import json_normalize

# Load the JSON data from the file
#with open('path_to_your_file/output1.json', 'r') as file:
#    json_data = json.load(file)
report_data1=report_data
# Normalize the primary data
df_reports = json_normalize(report_data1, record_path=['reports'])

# Extract and normalize nested data (e.g., 'updates')
# We will create a separate DataFrame for updates and then merge it with the main DataFrame
# Assuming each report can have multiple updates

# Create an empty DataFrame for updates
df_updates = pd.DataFrame()

for report in report_data1['reports']:
    # Normalize updates for each report
    df_report_updates = json_normalize(report, record_path='updates', 
                                       meta='id', 
                                       errors='ignore')

    # Append to the main updates DataFrame
    df_updates = pd.concat([df_updates, df_report_updates], ignore_index=True)


# Merge the updates DataFrame with the reports DataFrame
# Using 'id' as the key to join on
df_merged = pd.merge(df_reports, df_updates, on='id', how='left')

# Show the first few rows of the merged DataFrame
print(df_merged.head())


        id            current_datetime   latitude  longitude  \
0  5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
1  5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
2  5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
3  5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
4  5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   

                                  problem_header  \
0  Long series of potholes on south side of road   
1  Long series of potholes on south side of road   
2  Long series of potholes on south side of road   
3  Long series of potholes on south side of road   
4  Long series of potholes on south side of road   

                                    report_meta_info  \
0  \n        Reported via desktop in the A pothol...   
1  \n        Reported via desktop in the A pothol...   
2  \n        Reported via desktop in the A pothol...   
3  \n        Reported via desktop in the A pothol...   
4  \n        Reported 

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

...

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_updates = df_updates.append(df_report_updates, ignore_index=True)
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_9276\1308400837.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future

        id            current_datetime   latitude longitude  \
0  5118394  2024-03-13 10:38:42.779169  51.887275  -2.05617   
1  5118394  2024-03-13 10:38:42.779169  51.887275  -2.05617   
2  5118394  2024-03-13 10:38:42.779169  51.887275  -2.05617   
3  5118394  2024-03-13 10:38:42.779169  51.887275  -2.05617   
4  5118394  2024-03-13 10:38:42.779169  51.887275  -2.05617   

                          problem_header  \
0  Loose/rattling cover/ironwork problem   
1  Loose/rattling cover/ironwork problem   
2  Loose/rattling cover/ironwork problem   
3  Loose/rattling cover/ironwork problem   
4  Loose/rattling cover/ironwork problem   

                                    report_meta_info  \
0  \n        Reported via Open311 in the Loose/ra...   
1  \n        Reported via Open311 in the Loose/ra...   
2  \n        Reported via Open311 in the Loose/ra...   
3  \n        Reported via Open311 in the Loose/ra...   
4  \n        Reported via Open311 in the Loose/ra...   

                   

In [11]:
print(df_merged)
#df_merged.to_csv('dfmerged_06_01_2024.csv', index=True)

            id            current_datetime   latitude  longitude  \
0      5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
1      5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
2      5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
3      5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
4      5677669  2024-04-09 10:08:27.507181  51.774658  -2.298807   
...        ...                         ...        ...        ...   
14373  5593873  2024-04-09 10:08:27.507181   51.70787  -2.181164   
14374  5664031  2024-04-09 10:08:27.507181  51.858173  -2.260637   
14375  5664031  2024-04-09 10:08:27.507181  51.858173  -2.260637   
14376  5664031  2024-04-09 10:08:27.507181  51.858173  -2.260637   
14377  5664031  2024-04-09 10:08:27.507181  51.858173  -2.260637   

                                      problem_header  \
0      Long series of potholes on south side of road   
1      Long series of potholes on south side of road   
2      Long ser

In [12]:
print(df_reports)
#print(df_updates)

           id            current_datetime          latitude  \
0     5677669  2024-04-09 10:08:27.507181         51.774658   
1     5721855  2024-04-09 10:08:27.507181  51.7386556999992   
2     5504443  2024-04-09 10:08:27.507181         51.788307   
3     5711940  2024-04-09 10:08:27.507181  51.7044840999996   
4     5823867  2024-04-09 10:08:27.507181   51.716053999999   
...       ...                         ...               ...   
5795  5590459  2024-04-09 10:08:27.507181         51.821416   
5796  5631802  2024-04-09 10:08:27.507181          51.91371   
5797  5588653  2024-04-09 10:08:27.507181         51.754719   
5798  5593873  2024-04-09 10:08:27.507181          51.70787   
5799  5664031  2024-04-09 10:08:27.507181         51.858173   

              longitude                                     problem_header  \
0             -2.298807      Long series of potholes on south side of road   
1     -2.52034330000003               TMC - Defects -CW10 Potholes problem   
2        

Convert raw date formats to a one format

In [14]:
import pandas as pd

# Sample dataframe
data = df_reports

dfnew = pd.DataFrame(data)

# Regex pattern for the date and time
date_pattern = r'(\d{1,2}:\d{2},\s(?:Monday|Mon|Tuesday|Tue|Wednesday|Wed|Thursday|Thu|Friday|Fri|Saturday|Sat|Sunday|Sun)\s+\d{1,2}\s(?:January|February|March|April|May|June|July|August|September|October|November|December)\s+\d{4})'
pattern = r'in the\s+(.+?)\s+(?:by|anonymously)'

# Extract the text into a new column
dfnew['category'] = dfnew['report_meta_info'].str.extract(pattern, expand=False)

# Extract date from the 'report_meta_info' column
dfnew['date'] = dfnew['report_meta_info'].str.extract(date_pattern)
# Convert the date strings to datetime objects
dfnew['date'] = pd.to_datetime(dfnew['date'], errors='coerce')

print(dfnew)


           id            current_datetime          latitude  \
0     5677669  2024-04-09 10:08:27.507181         51.774658   
1     5721855  2024-04-09 10:08:27.507181  51.7386556999992   
2     5504443  2024-04-09 10:08:27.507181         51.788307   
3     5711940  2024-04-09 10:08:27.507181  51.7044840999996   
4     5823867  2024-04-09 10:08:27.507181   51.716053999999   
...       ...                         ...               ...   
5795  5590459  2024-04-09 10:08:27.507181         51.821416   
5796  5631802  2024-04-09 10:08:27.507181          51.91371   
5797  5588653  2024-04-09 10:08:27.507181         51.754719   
5798  5593873  2024-04-09 10:08:27.507181          51.70787   
5799  5664031  2024-04-09 10:08:27.507181         51.858173   

              longitude                                     problem_header  \
0             -2.298807      Long series of potholes on south side of road   
1     -2.52034330000003               TMC - Defects -CW10 Potholes problem   
2        

In [15]:
dfnew.to_csv('transformed_csv.csv', index=True)

Convert status data in to column format

In [20]:
import pandas as pd
import json

# Your JSON data
json_str = '''
{
    "id": "5064540",
    "current_datetime": "2024-01-20 20:08:54.434258",
    "latitude": "51.700335",
    "longitude": "-2.347006",
    "problem_header": "Path not reinstated after ploughing problem",
    "report_meta_info": "\\n        Reported via Open311 in the Path not reinstated after ploughing category by Gloucestershire County Council at 10:29, Wed  4 October 2023\\n\\n\\n    ",
    "moderate_display": "\\nReporting:path_not_reinstated_after_ploughing",
    "banner": "\\n\\n            Investigating\\n        ",
    "updates": [{
        "update_id": 1,
        "update_number": "update_11725815",
        "moderate_display": [{
            "update": 1,
            "moderate_display": "\\n\\nThank you for your report, it has been assigned to our Public Rights of Way team for investigation.\\n"
        }],
        "meta_2": [{
            "update": 1, 
            "meta_2": "State changed to: Investigating"
        }, {
            "update": 2,
            "meta_2": "\\n    \\n\\n    \\n\\n    Posted by Gloucestershire County Council at 10:20, Thu  5 October 2023\\n\\n\\n  \\n  \\n  \\n"
        }]
    }]
}
'''

# Load JSON data
#data = json.loads(json_str)
data1 = report_data['reports']

# Initialize a DataFrame

df100 = pd.DataFrame()
t=0
print(type(data1))
for data in data1:
    df = pd.DataFrame()
    #print(data)
    # Extracting top-level data
    for key in data:
        if key != 'updates':
            df[key] = [data[key]]

    # Extracting data from 'updates'
    #print(data['updates'])
    for update in data['updates']:
        #print(update)
        k=0
        for key in update:
            if k==0:
                p=key
            k=1
            #print(key)
            #print('////')
            if key not in ['moderate_display', 'meta_2']:
                #print(f'updates_{key}_{update[p]}')
                df[f'updates_{key}_{update[p]}'] = [update[key]]
            else:
                j=0
                for item in update[key]:
                    [{
            "update": 1, 
            "meta_2": "State changed to: Investigating"
        }, {
            "update": 2,
            "meta_2": "\\n    \\n\\n    \\n\\n    Posted by Gloucestershire County Council at 10:20, Thu  5 October 2023\\n\\n\\n  \\n  \\n  \\n"
        }]

                    #print('aaaa')
                    #print(item)
                    for sub_key in item:
                        {
            "update": 1, 
            "meta_2": "State changed to: Investigating"
        }
                        if j==0:
                            q=sub_key
                        j=1
                        #print(f'updates_{update[p]}_{key}_{sub_key}_{item[q]}')
                        #updates_1_meta_2_meta_2_1
                        df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
    #print(df)                    
    df100 = pd.concat([df100, df], ignore_index=True,sort=False)
    #print(df100)
    t=t+1
    print(t)

df100.head()


<class 'list'>
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
2

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:63: PerformanceWarning: DataFrame is highly fragmented.  This is usually the resul

2509
2510
2511
2512
2513
2514
2515
2516
2517
2518
2519
2520
2521
2522
2523
2524
2525
2526
2527
2528
2529
2530
2531
2532
2533
2534
2535
2536
2537
2538
2539
2540
2541
2542
2543
2544
2545
2546
2547
2548
2549
2550
2551
2552
2553
2554
2555
2556
2557
2558
2559
2560
2561
2562
2563
2564
2565
2566
2567
2568
2569
2570
2571
2572
2573
2574
2575
2576
2577
2578
2579
2580
2581
2582
2583
2584
2585
2586
2587
2588
2589
2590
2591
2592
2593
2594
2595
2596
2597
2598
2599
2600
2601
2602
2603
2604
2605
2606
2607
2608
2609
2610
2611
2612
2613
2614
2615
2616
2617
2618
2619
2620
2621
2622
2623
2624
2625
2626
2627
2628
2629
2630
2631
2632
2633
2634
2635
2636
2637
2638
2639
2640
2641
2642
2643
2644
2645
2646
2647
2648
2649
2650
2651
2652
2653
2654
2655
2656
2657
2658
2659
2660
2661
2662
2663
2664
2665
2666
2667
2668
2669
2670
2671
2672
2673
2674
2675
2676
2677
2678
2679
2680
2681
2682
2683
2684
2685
2686
2687
2688
2689
2690
2691
2692
2693
2694
2695
2696
2697
2698
2699
2700
2701
2702
2703
2704
2705
2706
2707
2708


C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]


3343
3344
3345
3346
3347
3348
3349
3350
3351
3352
3353
3354
3355
3356
3357
3358
3359
3360
3361
3362
3363
3364
3365
3366
3367
3368
3369
3370
3371
3372
3373
3374
3375
3376
3377
3378
3379
3380
3381
3382
3383
3384
3385
3386
3387
3388
3389
3390
3391
3392
3393
3394
3395
3396
3397
3398
3399
3400
3401
3402
3403
3404
3405
3406
3407
3408
3409
3410
3411
3412
3413
3414
3415
3416
3417
3418
3419
3420
3421
3422
3423
3424
3425
3426
3427
3428
3429
3430
3431
3432
3433
3434
3435
3436
3437
3438
3439
3440
3441
3442
3443
3444
3445
3446
3447
3448
3449
3450
3451
3452
3453
3454
3455
3456
3457
3458
3459
3460
3461
3462
3463
3464
3465
3466
3467
3468
3469
3470
3471
3472
3473
3474
3475
3476
3477
3478
3479
3480
3481
3482
3483
3484
3485
3486
3487
3488
3489
3490
3491
3492
3493
3494
3495
3496
3497
3498
3499
3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542


...

C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:63: PerformanceWarning: DataFrame is highly fragmented.  This is usually the resul

4558
4559
4560
4561
4562
4563
4564
4565
4566
4567
4568
4569
4570
4571
4572
4573
4574
4575
4576
4577
4578
4579
4580
4581
4582
4583
4584
4585
4586
4587
4588
4589
4590
4591
4592
4593
4594
4595
4596
4597
4598
4599
4600
4601
4602
4603
4604
4605
4606
4607
4608
4609
4610
4611
4612
4613
4614
4615
4616
4617
4618
4619
4620
4621
4622
4623
4624
4625
4626
4627
4628
4629
4630
4631
4632
4633
4634
4635
4636
4637
4638
4639
4640
4641
4642
4643
4644
4645
4646
4647
4648
4649
4650
4651
4652
4653
4654
4655
4656
4657
4658
4659
4660
4661
4662
4663
4664
4665
4666
4667
4668
4669
4670
4671
4672
4673
4674
4675
4676
4677
4678
4679
4680
4681
4682
4683
4684
4685
4686
4687
4688
4689
4690
4691
4692
4693
4694
4695
4696
4697
4698
4699
4700
4701
4702
4703
4704
4705
4706
4707
4708
4709
4710
4711
4712
4713
4714
4715
4716
4717
4718
4719
4720
4721
4722
4723
4724
4725
4726
4727
4728
4729
4730
4731
4732
4733
4734
4735
4736
4737
4738
4739
4740
4741
4742
4743
4744
4745
4746
4747
4748
4749
4750
4751
4752
4753
4754
4755
4756
4757


C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:87: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'updates_{update[p]}_{key}_{sub_key}_{item[q]}'] = [item[sub_key]]
C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1205854049.py:63: PerformanceWarning: DataFrame is highly fragmented.  This is usually the resul

5610
5611
5612
5613
5614
5615
5616
5617
5618
5619
5620
5621
5622
5623
5624
5625
5626
5627
5628
5629
5630
5631
5632
5633
5634
5635
5636
5637
5638
5639
5640
5641
5642
5643
5644
5645
5646
5647
5648
5649
5650
5651
5652
5653
5654
5655
5656
5657
5658
5659
5660
5661
5662
5663
5664
5665
5666
5667
5668
5669
5670
5671
5672
5673
5674
5675
5676
5677
5678
5679
5680
5681
5682
5683
5684
5685
5686
5687
5688
5689
5690
5691
5692
5693
5694
5695
5696
5697
5698
5699
5700
5701
5702
5703
5704
5705
5706
5707
5708
5709
5710
5711
5712
5713
5714
5715
5716
5717
5718
5719
5720
5721
5722
5723
5724
5725
5726
5727
5728
5729
5730
5731
5732
5733
5734
5735
5736
5737
5738
5739
5740
5741
5742
5743
5744
5745
5746
5747
5748
5749
5750
5751
5752
5753
5754
5755
5756
5757
5758
5759
5760
5761
5762
5763
5764
5765
5766
5767
5768
5769
5770
5771
5772
5773
5774
5775
5776
5777
5778
5779
5780
5781
5782
5783
5784
5785
5786
5787
5788
5789
5790
5791
5792
5793
5794
5795
5796
5797
5798
5799
5800


id            current_datetime          latitude          longitude  \
0  5677669  2024-04-09 10:08:27.507181         51.774658          -2.298807   
1  5721855  2024-04-09 10:08:27.507181  51.7386556999992  -2.52034330000003   
2  5504443  2024-04-09 10:08:27.507181         51.788307          -2.192692   
3  5711940  2024-04-09 10:08:27.507181  51.7044840999996         -1.9186407   
4  5823867  2024-04-09 10:08:27.507181   51.716053999999  -2.64193760000011   

                                      problem_header  \
0      Long series of potholes on south side of road   
1               TMC - Defects -CW10 Potholes problem   
2  Triangular section of highway verge completely...   
3               TMC - Defects -CW10 Potholes problem   
4               TMC - Defects -CW10 Potholes problem   

                                    report_meta_info  \
0  \n        Reported via desktop in the A pothol...   
1  \n        Reported via Open311 in the TMC - De...   
2  \n        Reported via desktop in the Causing ...   
3  \n        Reported via Open311 in the TMC - De...   
4  \n        Reported via Open311 in the TMC - De...   

                                    moderate_display  \
0  \nOpposite new moreton farm from start of the ...   
1  \nC way pothole 1000 400 50 give and take 15DB...   
2  \nCorner of A46 and Pullens roadnext to house ...   
3  \nCWPH \n500 X 400 X 50 mm\n15DB NARROW ROAD \...   
4  \nC way pothole 900 400 60 give and take 15DB ...   

                                       banner  updates_update_id_1  \
0  \n\n            Action scheduled\n                          1.0   
1       \n\n            In progress\n                          1.0   
2  \n\n            Action scheduled\n                          1.0   
3       \n\n            In progress\n                          1.0   
4             \n\n            Fixed\n                          1.0   

  updates_update_number_1  ...  updates_20_meta_2_update_2  \
0         update_13722736  ...                         NaN   
1         update_14159186  ...                         NaN   
2         update_13121226  ...                         NaN   
3         update_14158655  ...                         NaN   
4         update_14155765  ...                         NaN   

  updates_20_meta_2_meta_2_2  updates_update_id_21 updates_update_number_21  \
0                        NaN                   NaN                      NaN   
1                        NaN                   NaN                      NaN   
2                        NaN                   NaN                      NaN   
3                        NaN                   NaN                      NaN   
4                        NaN                   NaN                      NaN   

   updates_21_moderate_display_update_1  \
0                                   NaN   
1                                   NaN   
2                                   NaN   
3                                   NaN   
4                                   NaN   

  updates_21_moderate_display_moderate_display_1  updates_21_meta_2_update_1  \
0                                            NaN                         NaN   
1                                            NaN                         NaN   
2                                            NaN                         NaN   
3                                            NaN                         NaN   
4                                            NaN                         NaN   

  updates_21_meta_2_meta_2_1  updates_21_meta_2_update_2  \
0                        NaN                         NaN   
1                        NaN                         NaN   
2                        NaN                         NaN   
3                        NaN                         NaN   
4                        NaN                         NaN   

  updates_21_meta_2_meta_2_2  
0                        NaN  
1                        NaN  
2                        NaN  
3                        NaN

Extract Last update date

In [22]:
set1=['updates_2_meta_2_meta_2_1','updates_3_meta_2_meta_2_1','updates_4_meta_2_meta_2_1','updates_5_meta_2_meta_2_1','updates_6_meta_2_meta_2_1','updates_7_meta_2_meta_2_1','updates_8_meta_2_meta_2_1','updates_9_meta_2_meta_2_1','updates_10_meta_2_meta_2_1','updates_11_meta_2_meta_2_1','updates_12_meta_2_meta_2_1','updates_13_meta_2_meta_2_1','updates_14_meta_2_meta_2_1','updates_15_meta_2_meta_2_1','updates_16_meta_2_meta_2_1','updates_17_meta_2_meta_2_1','updates_18_meta_2_meta_2_1','updates_19_meta_2_meta_2_1']
set2=['updates_2_meta_2_meta_2_2','updates_3_meta_2_meta_2_2','updates_4_meta_2_meta_2_2','updates_5_meta_2_meta_2_2','updates_6_meta_2_meta_2_2','updates_7_meta_2_meta_2_2','updates_8_meta_2_meta_2_2','updates_9_meta_2_meta_2_2','updates_10_meta_2_meta_2_2','updates_11_meta_2_meta_2_2','updates_12_meta_2_meta_2_2','updates_13_meta_2_meta_2_2','updates_14_meta_2_meta_2_2','updates_15_meta_2_meta_2_2','updates_16_meta_2_meta_2_2','updates_17_meta_2_meta_2_2','updates_18_meta_2_meta_2_2','updates_19_meta_2_meta_2_2']
i=set1[0]
df100['closed_date']= 'Nan'
df100[i]=df100[i].fillna('Nan')
for idx in df100.index:
    
    j=1
    while j>0:
        k=j-1
        df100[set1[k]]=df100[set1[k]].fillna('Nan')
        df100[set2[k]]=df100[set2[k]].fillna('Nan')
        row2=df100.loc[idx,set1[k]]
        #print(row2)
        if row2!=0:
            #print(type(row2))
                printable = r'\w \!\"#\$%&\'\(\)\*\+,\-\./:;<»«؛،ـ\=>\?@\[\\\]\^_\`\{\|\}~'
                row2= row2.replace(r'[^{}]+'.format(printable), '')
                row2=row2.replace('\n', '').replace('\t', '')
                #print(df100.loc[idx,'id'],row2)
                pattern = 'Closed|No further action'
                if "Closed".lower() in row2.lower() or "No further action".lower() in row2.lower() or "Fixed".lower() in row2.lower():
                    #print('k')
                    print(df100.loc[idx,'id'],df100.loc[idx,set2[0]],row2)
                    df100.at[idx, 'closed_date']=df100.loc[idx,set2[0]]
                    j=0
                else:
                    if j<=12:
                        j=j+1
                    else:
                        j=0
                 #   print(df100.loc[idx,'id'],row2)




C:\Users\Lenovo 2022\AppData\Local\Temp\ipykernel_19732\1200062992.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df100['closed_date']= 'Nan'


5823867 
    

    

    Updated by Gloucestershire County Council at 09:50 today


  
  
  
 State changed to: Fixed
5799809 
    

    

    Posted by Gloucestershire County Council at 09:47, Wednesday  3 April 2024


  
  
  
 State changed to: Fixed
5709044 
    

    

    Posted by Gloucestershire County Council at 09:17, Friday 15 March 2024


  
  
  
 State changed to: Fixed
5813843 
    

    

    Posted by Gloucestershire County Council at 09:39 today


  
  
  
 State changed to: Closed
5821500 
    

    

    Posted by Gloucestershire County Council at 09:37 today


  
  
  
 State changed to: Closed
5689024 
    

    

    Posted by Gloucestershire County Council at 13:43, Monday 11 March 2024


  
  
  
 State changed to: Fixed
5824704 
    

    

    Updated by Gloucestershire County Council at 09:39 today


  
  
  
 State changed to: Closed
5823866 
    

    

    Updated by Gloucestershire County Council at 09:44 today


  
  
  
 State changed to: Fixed
5824703

In [23]:
import re
from datetime import datetime
from datetime import datetime, timedelta

# Function to calculate the date
def interpret_date(text, reference_date_str):
    # Parse the reference date
    reference_date = datetime.strptime(reference_date_str, "%Y-%m-%d %H:%M:%S.%f")
    
    # Today's date based on the reference
    if 'today' in text:
        interpreted_date = reference_date
    # Yesterday's date based on the reference
    elif 'yesterday' in text:
        interpreted_date = reference_date - timedelta(days=1)
    # A specific weekday (e.g., Wednesday) based on the reference
    elif 'Wednesday' in text:
        # Find the last Wednesday relative to the reference date
        weekday = 2  # Monday is 0, Sunday is 6
        days_behind = (reference_date.weekday() - weekday) % 7
        interpreted_date = reference_date - timedelta(days=days_behind)
        if interpreted_date > reference_date:
            # If the calculated date is in the future, subtract a week
            interpreted_date -= timedelta(days=7)
    elif 'Monday' in text:
        # Find the last Wednesday relative to the reference date
        weekday = 0  # Monday is 0, Sunday is 6
        days_behind = (reference_date.weekday() - weekday) % 7
        interpreted_date = reference_date - timedelta(days=days_behind)
        if interpreted_date > reference_date:
            # If the calculated date is in the future, subtract a week
            interpreted_date -= timedelta(days=7)
    elif 'Tuesday' in text:
        # Find the last Wednesday relative to the reference date
        weekday = 1  # Monday is 0, Sunday is 6
        days_behind = (reference_date.weekday() - weekday) % 7
        interpreted_date = reference_date - timedelta(days=days_behind)
        if interpreted_date > reference_date:
            # If the calculated date is in the future, subtract a week
            interpreted_date -= timedelta(days=7)
    elif 'Sunday' in text:
        # Find the last Wednesday relative to the reference date
        weekday = -1  # Monday is 0, Sunday is 6
        days_behind = (reference_date.weekday() - weekday) % 7
        interpreted_date = reference_date - timedelta(days=days_behind)
        if interpreted_date > reference_date:
            # If the calculated date is in the future, subtract a week
            interpreted_date -= timedelta(days=7)
    elif 'Saturday' in text:
        # Find the last Wednesday relative to the reference date
        weekday = -2  # Monday is 0, Sunday is 6
        days_behind = (reference_date.weekday() - weekday) % 7
        interpreted_date = reference_date - timedelta(days=days_behind)
        if interpreted_date > reference_date:
            # If the calculated date is in the future, subtract a week
            interpreted_date -= timedelta(days=7)
    else:
        # If no recognizable term is found
        interpreted_date = None

    return interpreted_date.strftime("%d/%m/%Y") if interpreted_date else reference_date.strftime("%d/%m/%Y")

# Test the function
reference_date_str = "08/03/2024 13:32:41"
texts = [
    "Updated by Gloucestershire County Council at 16:08, Saturday",
    "Updated by Gloucestershire County Council at 16:08 today",
    "Updated by Gloucestershire County Council at 16:08 yesterday",
    "Updated by Gloucestershire County Council at 16:08, Wednesday 14 February 2024",
]


df100['closed_date1']=pd.NA
for idx in df100.index:
    row2=df100.loc[idx,'closed_date']
    date_pattern = r'(\d{1,2})\s+(January|February|March|April|May|June|July|August|September|October|November|December)\s+(\d{4})'
    match = re.search(date_pattern, row2)
    #print(idx,row2)
    if match:
        extracted_date_str = f"{match.group(1)} {match.group(2)} {match.group(3)}"
        print(datetime.strptime(extracted_date_str,"%d %B %Y").strftime("%d/%m/%Y"))
        df100.at[idx, 'closed_date1']=datetime.strptime(extracted_date_str,"%d %B %Y").strftime("%d/%m/%Y")
    else:
        #extracted_date_str = None
        #print(f"Text: {row2}")
        df100.at[idx, 'closed_date1']=interpret_date(row2, df100.loc[idx,'current_datetime'])
        print(interpret_date(row2, df100.loc[idx,'current_datetime']))



09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
03/04/2024
09/04/2024
15/03/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
11/03/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024
09/04/2024

13/03/2024
18/12/2023
13/03/2024
08/12/2023
18/12/2023
13/03/2024
21/11/2023
19/10/2023
13/03/2024
15/12/2023
18/12/2023
15/12/2023
05/12/2023
13/03/2024
13/03/2024
29/11/2023
13/03/2024
13/03/2024
18/12/2023
18/12/2023
27/11/2023
18/12/2023
13/03/2024
13/03/2024
13/03/2024
22/11/2023
15/12/2023
13/03/2024
15/12/2023
11/12/2023
15/12/2023
13/03/2024
13/03/2024
15/12/2023
01/12/2023
07/12/2023
30/11/2023
11/12/2023
05/12/2023
08/12/2023
17/11/2023
11/12/2023
04/12/2023
30/11/2023
11/12/2023
08/12/2023
11/12/2023
11/12/2023
13/03/2024
07/12/2023
11/12/2023
14/11/2023
08/12/2023
04/12/2023
13/03/2024
29/11/2023
04/12/2023
11/12/2023
30/11/2023
30/11/2023
11/12/2023
08/12/2023
05/12/2023
05/12/2023
06/12/2023
01/12/2023
04/12/2023
07/12/2023
07/12/2023
07/12/2023
27/11/2023
30/11/2023
11/12/2023
30/11/2023
11/12/2023
11/12/2023
14/12/2023
15/12/2023
17/11/2023
30/11/2023
11/12/2023
04/12/2023
13/03/2024
04/12/2023
11/12/2023
11/12/2023
14/12/2023
13/03/2024
08/12/2023
11/12/2023
15/12/2023

30/10/2023
08/11/2023
13/03/2024
13/03/2024
13/11/2023
13/03/2024
10/11/2023
10/11/2023
13/03/2024
24/10/2023
23/10/2023
13/03/2024
10/10/2023
13/11/2023
13/11/2023
10/11/2023
13/03/2024
01/11/2023
13/03/2024
30/10/2023
13/03/2024
06/11/2023
20/10/2023
08/11/2023
13/03/2024
13/11/2023
09/11/2023
13/03/2024
13/03/2024
06/11/2023
13/11/2023
28/10/2023
13/11/2023
09/11/2023
13/03/2024
13/03/2024
10/11/2023
13/03/2024
06/11/2023
02/11/2023
13/11/2023
13/03/2024
13/11/2023
13/03/2024
18/10/2023
13/03/2024
08/11/2023
13/03/2024
13/03/2024
06/11/2023
13/03/2024
13/03/2024
13/03/2024
01/11/2023
13/03/2024
13/03/2024
09/11/2023
07/11/2023
13/03/2024
13/03/2024
26/10/2023
11/10/2023
13/03/2024
06/11/2023
01/11/2023
10/11/2023
09/11/2023
27/10/2023
31/10/2023
13/03/2024
13/03/2024
01/11/2023
07/11/2023
13/03/2024
06/11/2023
13/03/2024
07/11/2023
09/11/2023
08/11/2023
13/03/2024
13/03/2024
13/03/2024
13/03/2024
13/03/2024
07/11/2023
13/03/2024
07/11/2023
13/03/2024
13/03/2024
13/03/2024
13/03/2024

In [24]:
df100

id            current_datetime          latitude  \
0     5677669  2024-04-09 10:08:27.507181         51.774658   
1     5721855  2024-04-09 10:08:27.507181  51.7386556999992   
2     5504443  2024-04-09 10:08:27.507181         51.788307   
3     5711940  2024-04-09 10:08:27.507181  51.7044840999996   
4     5823867  2024-04-09 10:08:27.507181   51.716053999999   
...       ...                         ...               ...   
5795  5590459  2024-04-09 10:08:27.507181         51.821416   
5796  5631802  2024-04-09 10:08:27.507181          51.91371   
5797  5588653  2024-04-09 10:08:27.507181         51.754719   
5798  5593873  2024-04-09 10:08:27.507181          51.70787   
5799  5664031  2024-04-09 10:08:27.507181         51.858173   

              longitude                                     problem_header  \
0             -2.298807      Long series of potholes on south side of road   
1     -2.52034330000003               TMC - Defects -CW10 Potholes problem   
2             -2.192692  Triangular section of highway verge completely...   
3            -1.9186407               TMC - Defects -CW10 Potholes problem   
4     -2.64193760000011               TMC - Defects -CW10 Potholes problem   
...                 ...                                                ...   
5795          -2.499786                       Pothole which is washing out   
5796          -2.117753                          Pothole 11 Springbank Way   
5797          -2.231814                                  Near to number 16   
5798          -2.181164                              Large pothole in rode   
5799          -2.260637                   Deeper than a tennis ball hole!!   

                                       report_meta_info  \
0     \n        Reported via desktop in the A pothol...   
1     \n        Reported via Open311 in the TMC - De...   
2     \n        Reported via desktop in the Causing ...   
3     \n        Reported via Open311 in the TMC - De...   
4     \n        Reported via Open311 in the TMC - De...   
...                                                 ...   
5795  \n        Reported via desktop in the A pothol...   
5796  \n        Reported via iOS in the A pothole in...   
5797  \n        Reported via desktop in the A pothol...   
5798  \n        Reported via Android in the A pothol...   
5799  \n        Reported via mobile in the A pothole...   

                                       moderate_display  \
0     \nOpposite new moreton farm from start of the ...   
1     \nC way pothole 1000 400 50 give and take 15DB...   
2     \nCorner of A46 and Pullens roadnext to house ...   
3     \nCWPH \n500 X 400 X 50 mm\n15DB NARROW ROAD \...   
4     \nC way pothole 900 400 60 give and take 15DB ...   
...                                                 ...   
5795                                          \nO/s 11a   
5796                        \nOutside 11 Springbank Way   
5797              \n2 deep potholes with loose hardcore   
5798             \nOutside 7 Summersfield Road, gl6 9jx   
5799  \nThe potholes of which were golf ball depth a...   

                                          banner  updates_update_id_1  \
0     \n\n            Action scheduled\n                          1.0   
1          \n\n            In progress\n                          1.0   
2     \n\n            Action scheduled\n                          1.0   
3          \n\n            In progress\n                          1.0   
4                \n\n            Fixed\n                          1.0   
...                                          ...                  ...   
5795             \n\n            Fixed\n                          1.0   
5796             \n\n            Fixed\n                          1.0   
5797             \n\n            Fixed\n                          1.0   
5798             \n\n            Fixed\n                          1.0   
5799             \n\n            Fixed\n                          1.0   

     updates_update_nu

In [25]:
df100.to_csv('Treated_dataset_closed_date.csv', index=True)

In [31]:
new_df = pd.DataFrame(index=dfnew.index)

# Iterate over the rows in df
for idx in dfnew.index:
    # Directly copy the values using the index
    row2=dfnew.loc[idx,'latitude']
    row3=dfnew.loc[idx,'longitude']
    data = api1.get_nearest_postcodes_for_coordinates(latitude=row2,longitude=row3,limit=1,radius=1000)
    new_df.at[idx, 'id'] = dfnew.at[idx, 'id']
    if data['result'] is None:
        new_df.at[idx, 'postcode'] = 'NA'
    else:
        new_df.at[idx, 'postcode'] = data['result'][0]['postcode']
#for index, row in dfnew.iterrows():
    #print(row[2])
 #   data = api1.get_nearest_postcodes_for_coordinates(latitude=row[2],longitude=row[3],limit=1,radius=1000)
    #print(data)
  #  ndf=row[0]+data['result'][0]['postcode']
    #print(data['result'][0]['postcode'])

In [32]:
new_df

id  postcode
0     5677669  GL10 3DW
1     5721855  GL15 4EU
2     5504443   GL6 6XN
3     5711940   GL7 5PS
4     5823867  GL15 6US
...       ...       ...
5795  5590459  GL14 2NT
5796  5631802  GL51 0QZ
5797  5588653   GL5 4DE
5798  5593873   GL6 9JX
5799  5664031   GL2 5JD

[5800 rows x 2 columns]

In [33]:
combined_df1 = pd.merge(dfnew,new_df, on='id')

In [34]:
combined_df1.to_csv('combined_data_set.csv', index=True)

In [35]:
combined_df1

id            current_datetime          latitude  \
0     5677669  2024-04-09 10:08:27.507181         51.774658   
1     5721855  2024-04-09 10:08:27.507181  51.7386556999992   
2     5504443  2024-04-09 10:08:27.507181         51.788307   
3     5711940  2024-04-09 10:08:27.507181  51.7044840999996   
4     5823867  2024-04-09 10:08:27.507181   51.716053999999   
...       ...                         ...               ...   
5795  5590459  2024-04-09 10:08:27.507181         51.821416   
5796  5631802  2024-04-09 10:08:27.507181          51.91371   
5797  5588653  2024-04-09 10:08:27.507181         51.754719   
5798  5593873  2024-04-09 10:08:27.507181          51.70787   
5799  5664031  2024-04-09 10:08:27.507181         51.858173   

              longitude                                     problem_header  \
0             -2.298807      Long series of potholes on south side of road   
1     -2.52034330000003               TMC - Defects -CW10 Potholes problem   
2             -2.192692  Triangular section of highway verge completely...   
3            -1.9186407               TMC - Defects -CW10 Potholes problem   
4     -2.64193760000011               TMC - Defects -CW10 Potholes problem   
...                 ...                                                ...   
5795          -2.499786                       Pothole which is washing out   
5796          -2.117753                          Pothole 11 Springbank Way   
5797          -2.231814                                  Near to number 16   
5798          -2.181164                              Large pothole in rode   
5799          -2.260637                   Deeper than a tennis ball hole!!   

                                       report_meta_info  \
0     \n        Reported via desktop in the A pothol...   
1     \n        Reported via Open311 in the TMC - De...   
2     \n        Reported via desktop in the Causing ...   
3     \n        Reported via Open311 in the TMC - De...   
4     \n        Reported via Open311 in the TMC - De...   
...                                                 ...   
5795  \n        Reported via desktop in the A pothol...   
5796  \n        Reported via iOS in the A pothole in...   
5797  \n        Reported via desktop in the A pothol...   
5798  \n        Reported via Android in the A pothol...   
5799  \n        Reported via mobile in the A pothole...   

                                       moderate_display  \
0     \nOpposite new moreton farm from start of the ...   
1     \nC way pothole 1000 400 50 give and take 15DB...   
2     \nCorner of A46 and Pullens roadnext to house ...   
3     \nCWPH \n500 X 400 X 50 mm\n15DB NARROW ROAD \...   
4     \nC way pothole 900 400 60 give and take 15DB ...   
...                                                 ...   
5795                                          \nO/s 11a   
5796                        \nOutside 11 Springbank Way   
5797              \n2 deep potholes with loose hardcore   
5798             \nOutside 7 Summersfield Road, gl6 9jx   
5799  \nThe potholes of which were golf ball depth a...   

                                          banner  \
0     \n\n            Action scheduled\n           
1          \n\n            In progress\n           
2     \n\n            Action scheduled\n           
3          \n\n            In progress\n           
4                \n\n            Fixed\n           
...                                          ...   
5795             \n\n            Fixed\n           
5796             \n\n            Fixed\n           
5797             \n\n            Fixed\n           
5798             \n\n            Fixed\n           
5799             \n\n            Fixed\n           

                                                updates  \
0     [{'update_id': 1, 'update_number': 'update_137...   
1     [{'update_id': 1, 'update_number': 'update_141...   
2     [{'update_id': 1, 'update_number': 'update_131...   
3     [{'update_id': 1, 'update_number